In [8]:
import pathlib as path
from collections import defaultdict
from pathlib import Path

import numpy as np
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
from lxml import etree as et
from plotly.offline import iplot
from scipy.interpolate import griddata

# Create Surface Plots
To plot 3D surface plot, we need a 2 dimension array for the z values. In this case, our horizon data is in 3D points form (i.e. each point has one x,y and z values). There are multiple ways to triangulate/interpolate surfaces from these points cloud. Thus, plotting 3D surfaces require the z to be in a 2 dimensional array.

The regrid function below resamples the x and y to the *step* value which we set to 64. It can be set higher for more resolution, but since we need to calculate the z for each of these values, it can be computationally taxing.

In [76]:
def regrid(df, step=64):
    x1 = np.linspace(df["X"].min(), df["X"].max(), step)
    y1 = np.linspace(df["Y"].min(), df["Y"].max(), step)
    x2, y2 = np.meshgrid(x1, y1)
    z2 = griddata((df["X"], df["Y"]), df["Z"], (x2, y2), method="cubic")
    return x2, y2, z2


def get_stacked_minmax(*kwargs):
    # print(kwargs)
    stacked = np.r_[kwargs]
    return stacked

In [77]:
# Read data from a csv
horizon_dir = Path.cwd().joinpath("horizon")
bcu = pd.read_csv(horizon_dir / "BCU.csv")
hugin_base = pd.read_csv(horizon_dir / "Hugin_Base.csv")
hugin_top = pd.read_csv(horizon_dir / "Hugin_Fm_top.csv")
shetland = pd.read_csv(horizon_dir / "SHETLAND.csv")
ty = pd.read_csv(horizon_dir / "Ty.csv")

bcu_x, bcu_y, bcu_z = regrid(bcu)
hugin_base_x, hugin_base_y, hugin_base_z = regrid(hugin_base)
hugin_top_x, hugin_top_y, hugin_top_z = regrid(hugin_top)
shetland_x, shetland_y, shetland_z = regrid(shetland)
ty_x, ty_y, ty_z = regrid(ty)

In [78]:
bcu_z[~np.isnan(bcu_z)].shape

(2719,)

In [79]:
stack = get_stacked_minmax(bcu_z, hugin_base_z, hugin_top_z, shetland_z, ty_z)
shared_z_min = -np.nanmax(stack)
shared_z_max = -np.nanmin(stack)

In [95]:
bcu_surface = go.Surface(
    z=-bcu_z,
    x=bcu_x,
    y=bcu_y,
    cmin=shared_z_min,
    cmax=shared_z_max,
)

hugin_base_surface = go.Surface(
    z=-hugin_base_z,
    x=hugin_base_x,
    y=hugin_base_y,
    cmin=shared_z_min,
    cmax=shared_z_max,
)

hugin_top_surface = go.Surface(
    z=-hugin_top_z,
    x=hugin_top_x,
    y=hugin_top_y,
    cmin=shared_z_min,
    cmax=shared_z_max,
)

shetland_surface = go.Surface(
    z=-shetland_z,
    x=shetland_x,
    y=shetland_y,
    cmin=shared_z_min,
    cmax=shared_z_max,
)

ty_surface = go.Surface(
    z=-ty_z,
    x=ty_x,
    y=ty_y,
    cmin=shared_z_min,
    cmax=shared_z_max,
)

horizon_plot = go.Figure(
    data=[
        bcu_surface,
        hugin_base_surface,
        hugin_top_surface,
        shetland_surface,
        ty_surface,
    ]
)

horizon_plot.update_layout(
    width=800,
    height=500,
)

horizon_plot.update_scenes(zaxis_rangemode="tozero")

iplot(horizon_plot)

# Create Well Trajectory Plot

## Read data from WITSML

In [69]:
witsml_dir = Path.cwd().joinpath("witsml")

In [70]:
data = defaultdict(list)
for file in witsml_dir.rglob("1.xml"):
    tree = et.parse(str(file))
    for elem in tree.getiterator():
        elem.tag = et.QName(elem).localname
    for traj in tree.findall("trajectory/trajectoryStation"):
        # data['filename'].append(str(file))
        data["nameWell"].append(tree.find("trajectory/nameWell").text)
        data["y"].append(float(traj.find("dispNs").text))
        data["x"].append(float(traj.find("dispEw").text))
        data["z"].append(float(traj.find("tvd").text) * -1)
        data["incl"].append(traj.find("incl").text)

In [86]:
trajectory = pd.DataFrame(data)

trajectory.loc[trajectory["nameWell"] == "15/9-F-10", "x"] = (
    trajectory.loc[trajectory["nameWell"] == "15/9-F-10", "x"] + 435052.3
)
trajectory.loc[trajectory["nameWell"] == "15/9-F-10", "y"] = (
    trajectory.loc[trajectory["nameWell"] == "15/9-F-10", "y"] + 6478559.6
)

trajectory.loc[trajectory["nameWell"] == "15/9-F-4", "x"] = (
    trajectory.loc[trajectory["nameWell"] == "15/9-F-4", "x"] + 435049.8
)
trajectory.loc[trajectory["nameWell"] == "15/9-F-4", "y"] = (
    trajectory.loc[trajectory["nameWell"] == "15/9-F-4", "y"] + 6478560.8
)

trajectory.loc[trajectory["nameWell"] == "15/9-F-5", "x"] = (
    trajectory.loc[trajectory["nameWell"] == "15/9-F-5", "x"] + 435051.0
)
trajectory.loc[trajectory["nameWell"] == "15/9-F-5", "y"] = (
    trajectory.loc[trajectory["nameWell"] == "15/9-F-5", "y"] + 6478558.9
)

trajectory

nameWell             y              x            z   incl
0    15/9-F-10  6.478556e+06  435054.529917    -0.000000      0
1    15/9-F-10  6.478556e+06  435054.529917  -145.900140      0
2    15/9-F-10  6.478556e+06  435054.530255  -150.000005   0.02
3    15/9-F-10  6.478556e+06  435054.533108  -159.999883   0.05
4    15/9-F-10  6.478556e+06  435054.536891  -170.000066   0.04
..         ...           ...            ...          ...    ...
580   15/9-F-5  6.478391e+06  435239.027582 -1207.523722  30.29
581   15/9-F-5  6.478383e+06  435257.951729 -1242.614126  29.76
582   15/9-F-5  6.478376e+06  435276.027867 -1278.030362  28.07
583   15/9-F-5  6.478368e+06  435292.576299 -1314.037606  25.51
584   15/9-F-5  6.478366e+06  435297.542246 -1325.176217  27.26

[585 rows x 5 columns]

In [111]:
# trajectory = pd.DataFrame(data)
traj_plot = px.line_3d(trajectory, x="x", y="y", z="z", color="nameWell")

# traj_plot.update_layout(
#     width=800,
#     height=500,
# )

# iplot(traj_plot)

# Combining Horizon with Well Trajectory

In [119]:
combined_plot = go.Figure(
    data=[
        bcu_surface,
        hugin_base_surface,
        hugin_top_surface,
        shetland_surface,
        ty_surface,
        traj_plot.data[0],
        traj_plot.data[1],
        traj_plot.data[2]
    ]
)

combined_plot.update_layout(
    width=800,
    height=500,
)

iplot(combined_plot)

In [117]:
traj_plot.data[0]

Scatter3d({
    'hovertemplate': 'nameWell=15/9-F-10<br>x=%{x}<br>y=%{y}<br>z=%{z}<extra></extra>',
    'legendgroup': '15/9-F-10',
    'line': {'color': '#636efa', 'dash': 'solid'},
    'marker': {'symbol': 'circle'},
    'mode': 'lines',
    'name': '15/9-F-10',
    'scene': 'scene',
    'showlegend': True,
    'x': array([435054.5299168 , 435054.5299168 , 435054.53025452, ..., 437923.95758784,
                437948.72041614, 437973.6017647 ]),
    'y': array([6478555.6900256 , 6478555.6900256 , 6478555.69065654, ...,
                6476593.00426249, 6476571.56986512, 6476550.20743104]),
    'z': array([   -0.       ,  -145.90014  ,  -150.0000048, ..., -2952.1498488,
                -2975.5975032, -2999.0981928])
})